In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

/tmp/ipykernel_246607/3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [12]:
# Fetch NEAR USDT
sample = binance_recursive_fetch_2(
    ['SNX'],
    '1h',
    starttime=int(pd.to_datetime('2000-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot/futures data
)

print(sample['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-09-24 22:01:00 status : True, time : 1600984860000, limit : 2
2020-11-05 14:01:00 status : True, time : 1604584860000, limit : 4
2020-12-17 06:01:00 status : True, time : 1608184860000, limit : 6
2021-01-27 22:01:00 status : True, time : 1611784860000, limit : 8
2021-03-10 14:01:00 status : True, time : 1615384860000, limit : 10
2021-04-21 06:01:00 status : True, time : 1618984860000, limit : 12
2021-06-01 22:01:00 status : True, time : 1622584860000, limit : 14
2021-07-13 14:01:00 status : True, time : 1626184860000, limit : 16
2021-08-24 06:01:00 status : True, time : 1629784860000, limit : 18
2021-10-04 22:01:00 status : True, time : 1633384860000, limit : 20
2021-11-15 14:01:00 status : True, time : 1636984860000, limit : 22
2021-12-27 06:01:00 status : True, time : 1640584860000, limit : 24
2022-02-06 22:01:00 status : True, time : 1644184860000, limit : 26
2022-03-20 14:01:00 status : True, time : 1647784860000, limit : 28
2022-05-01 06:01:00 status : True, time : 1651384860

100%|██████████| 1/1 [00:04<00:00,  4.78s/it]

[['SNX', 1597388400000, '5.460', '5.890', '5.400', '5.668', '488330.4', 1597391999999, '2767005.9400', 10501, '313880.5', '1775297.1105', '0'], ['SNX', 1597392000000, '5.675', '5.903', '5.668', '5.764', '342288.8', 1597395599999, '1976337.3557', 6330, '157545.4', '909247.0695', '0'], ['SNX', 1597395600000, '5.772', '5.853', '5.702', '5.743', '273260.9', 1597399199999, '1576873.4176', 4521, '137661.4', '794941.4957', '0'], ['SNX', 1597399200000, '5.743', '5.852', '5.613', '5.699', '317264.6', 1597402799999, '1811057.6309', 5434, '144311.5', '824238.6837', '0'], ['SNX', 1597402800000, '5.699', '5.838', '5.600', '5.607', '273908.7', 1597406399999, '1567428.4290', 4143, '143967.5', '825199.3612', '0'], ['SNX', 1597406400000, '5.600', '5.652', '5.466', '5.494', '273605.1', 1597409999999, '1523598.9771', 5765, '131164.4', '731387.3120', '0'], ['SNX', 1597410000000, '5.496', '5.578', '5.471', '5.546', '221136.3', 1597413599999, '1220905.3367', 3500, '103683.5', '572471.3448', '0'], ['SNX', 15

In [13]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice    volume  \
0      SNX  1597388400000     5.460     5.890    5.400      5.668  488330.4   
1      SNX  1597392000000     5.675     5.903    5.668      5.764  342288.8   
2      SNX  1597395600000     5.772     5.853    5.702      5.743  273260.9   
3      SNX  1597399200000     5.743     5.852    5.613      5.699  317264.6   
4      SNX  1597402800000     5.699     5.838    5.600      5.607  273908.7   
...    ...            ...       ...       ...      ...        ...       ...   
38128  SNX  1734649200000     2.176     2.176    2.135      2.137  328109.0   
38129  SNX  1734652800000     2.136     2.184    2.102      2.171  682207.1   
38130  SNX  1734656400000     2.171     2.185    2.149      2.163  329096.9   
38131  SNX  1734660000000     2.164     2.241    2.160      2.227  724064.4   
38132  SNX  1734663600000     2.228     2.230    2.193      2.194  305355.8   

           closetime   quotevolume  trades taker_buy_volume taker_buy_quote  \
0      1597391999999  2767005.9400   10501         313880.5    1775297.1105   
1      1597395599999  1976337.3557    6330         157545.4     909247.0695   
2      1597399199999  1576873.4176    4521         137661.4     794941.4957   
3      1597402799999  1811057.6309    5434         144311.5     824238.6837   
4      1597406399999  1567428.4290    4143         143967.5     825199.3612   
...              ...           ...     ...              ...             ...   
38128  1734652799999   707789.9194    6512         140556.2     303336.7040   
38129  1734656399999  1462226.9327   10055         348344.5     748280.4098   
38130  1734659999999   713903.4901    6570         160882.7     348929.5461   
38131  1734663599999  1603132.5813   12517         413941.4     916872.0237   
38132  1734667199999   675264.3215    4781         176138.1     389634.7192   

      unused  
0          0  
1          0  
2          0  
3          0  
4          0  
...      ...  
38128      0  
38129      0  
38130      0  
38131      0  
38132      0  

[38133 rows x 13 columns]

In [14]:
# df.to_csv('SNX_USDT_futures_data_2020.csv', index=False)

# print("DataFrame has been saved to csv")

DataFrame has been saved to csv
